<center>
  
# TABDDPM: Modelling Tabular Data with Diffusion Models

</center>

Directly applying diffusion models to general tabular problems can be challenging because data points are typically represented by vectors of heterogeneous features. The inherent heterogeneity of tabular data complicates accurate modeling, as individual features can vary widely in nature; some may be continuous, while others are discrete. In this notebook, we explore **TabDDPM** — a diffusion model that can be universally applied to tabular datasets and effectively handles both categorical and numerical features.

Our primary focus in this work is synthetic data generation, which is in high demand for many tabular tasks. Firstly, tabular datasets are often limited in size, unlike vision or NLP problems where large amounts of additional data are readily available online. Secondly, properly generated synthetic datasets do not contain actual user data, thus avoiding GDPR-like regulations and allowing for public sharing without compromising anonymity.

In the following sections, we will delve deeper into the implementation of this method. The notebook is organized as follows:

1. [Imports and Setup]()


2. [Default Dataset]()

    2.1. [Download Data]()
    
    2.2. [Process Data]()
    
    2.3. [Review Data]()
    
    
3. [TabDDPM Algorithm]()
    
    3.1. [Load Config]()
    
    3.2. [Make Dataset]()
    
    3.3. [Instantiate Model]()
    
    3.4. [Train Model]()
    
    3.5. [Load Pretrained Model]()
    
    3.6. [Sample Data]()
    
    3.7. [Review Synthetic Data]()

# Imports and Setup

In this section, we import all necessary libraries and modules required for setting up the environment. This includes basic libraries for such numpy and pandas. We also import essential modules for data loading, model creation, and dataset downloading and processing dataset. We also specify list of possible datasets and their download URL in `NAME_URL_DICT_UCI` where you can use each of these datasets for the rest of this notebook. Furthermore based on `DATA_DIR` we specify path to raw and processed data in `RAW_DATA_DIR` and `PROCESSED_DATA_DIR` to further download the data and process it in a desired format.  Here we will focus on `"adult"` dataset thus we will specify it in `DATA_NAME`. 

In [1]:
import src
import json
import torch
import numpy as np
import pandas as pd
from pprint import pprint

from scripts.download_dataset import download_from_uci
from scripts.process_dataset import process_data

from src.data import make_dataset
from src.baselines.tabddpm.pipeline import TabDDPM


NAME_URL_DICT_UCI = {
    "adult": "https://archive.ics.uci.edu/static/public/2/adult.zip",
    "default": "https://archive.ics.uci.edu/static/public/350/default+of+credit+card+clients.zip",
    "magic": "https://archive.ics.uci.edu/static/public/159/magic+gamma+telescope.zip",
    "shoppers": "https://archive.ics.uci.edu/static/public/468/online+shoppers+purchasing+intention+dataset.zip",
    "beijing": "https://archive.ics.uci.edu/static/public/381/beijing+pm2+5+data.zip",
    "news": "https://archive.ics.uci.edu/static/public/332/online+news+popularity.zip",
}

# For shared directory you can change it to "/projects/aieng/diffusion_bootcamp/data/tabular"
DATA_DIR = "data"
RAW_DATA_DIR = f"{DATA_DIR}/raw_data"
PROCESSED_DATA_DIR = f"{DATA_DIR}/processed_data"
SYNTH_DATA_DIR = f"{DATA_DIR}/synthetic_data"
DATA_NAME = "default"

MODEL_PATH = "models/tabddpm"

# Default Dataset

In this section, we will download the **Default of Credit Card Clients** dataset from the UCI repository and load it into a pandas DataFrame. This dataset contains information on default payments, demographic factors, credit data, history of payment, and bill statements of credit card clients in Taiwan from April 2005 to September 2005. We will use this dataset to demonstrate the TabDDPM method.

## Download Data

We can download the required adult dataset to the specified directory in `RAW_DATA_DIR` using the download_from_uci function. This function takes the dataset name, the download path, and the URL of the data, and retrieves it from the UCI repository.

In [2]:
download_from_uci(DATA_NAME, RAW_DATA_DIR, NAME_URL_DICT_UCI)

Start processing dataset default from UCI.
Aready downloaded.


## Process Data

Now that we have downloaded the dataset, we need to process it into the desired CSV format using the `process_data` function. To do this, we provide the dataset name, the directory containing the information required for preprocessing, and the original data directory. The `INFO_DIR` contains a JSON file for each dataset, specifying the following:

1. task_type: This must be specified and can be binclass (binary classification) or regression, depending on the type of task for each dataset. For the adult dataset, the task type is binclass.
2. column_names: This is optional and contains the names of each column.
3. num_col_idx: This is necessary to specify the columns with numerical values.
4. cat_col_idx: This is necessary to specify the columns with categorical values.
5. target_col_idx: This is necessary to specify the column containing the target value for the regression or classification task.
6. file_type: This should be set to "csv" by default, as we want to preprocess the files as CSV.
7. data_path: Optional
8. test_path: Optional
9. column_info: Optional
10. train_num: Optional
11. test_num: Optional

The `process_data` function divides the raw data into training and test splits, saving them in `PROCESSED_DATA_DIR`. It also saves the processed information of the data as a JSON file in the same directory. Finally, it prints out general information about the training and test data after preprocessing, including:

1. Size of the training, validation, and test tables
2. Size of the numerical values in the training table
3. Size of the categorical values in the training table

In [3]:
INFO_DIR = "data_info"
process_data(DATA_NAME, INFO_DIR, DATA_DIR)

default (27000, 24) (3000, 24) (30000, 24)
Numerical (27000, 14)
Categorical (27000, 9)
Processing and Saving default Successfully!
default
Total 30000
Train 27000
Test 3000
Num 14
Cat 10


## Review Data

Following preprocessing, here we will review the train dataset.

Adult dataset consist of 24 columns in total where 14 columns are numerical and 10 columns are categorical. The target column is `default.payment.next.month` which is a binary classification task. The dataset contains 30000 rows in total. You can see 20 first rows of the dataset below.

In [4]:
df = pd.read_csv(f"{PROCESSED_DATA_DIR}/{DATA_NAME}/train.csv")

# Display the first few rows of the DataFrame
df.head(10)

LIMIT_BAL     SEX        EDUCATION MARRIAGE   AGE  \
0    20000.0  female       university  married  24.0   
1   200000.0  female       university  married  39.0   
2   230000.0  female       university   single  23.0   
3    50000.0  female  graduate school  married  35.0   
4   160000.0    male  graduate school  married  39.0   
5    20000.0    male      high school   others  59.0   
6    50000.0    male       university   single  42.0   
7   130000.0  female  graduate school   single  26.0   
8   300000.0  female       university  married  40.0   
9    20000.0    male       university  married  27.0   

                            PAY_0                           PAY_2  \
0  payment delay for three months  payment delay for three months   
1   payment delay for four months  payment delay for three months   
2                        pay duly                        pay duly   
3     payment delay for one month     payment delay for one month   
4                         unknown                         unknown   
5  payment delay for three months     payment delay for one month   
6     payment delay for one month     payment delay for one month   
7     payment delay for one month                        pay duly   
8     payment delay for one month     payment delay for one month   
9     payment delay for one month     payment delay for one month   

                            PAY_3                           PAY_4  \
0     payment delay for one month     payment delay for one month   
1  payment delay for three months  payment delay for three months   
2                        pay duly                        pay duly   
3     payment delay for one month                         unknown   
4                         unknown                         unknown   
5     payment delay for one month     payment delay for one month   
6     payment delay for one month     payment delay for one month   
7                        pay duly                        pay duly   
8     payment delay for one month     payment delay for one month   
9     payment delay for one month   payment delay for four months   

                            PAY_5  ... BILL_AMT4  BILL_AMT5  BILL_AMT6  \
0     payment delay for one month  ...   18457.0    21381.0    18914.0   
1  payment delay for three months  ...  125357.0   121853.0   124731.0   
2                        pay duly  ...    1045.0    12525.0    12219.0   
3                         unknown  ...       0.0        0.0        0.0   
4                         unknown  ...       0.0     2920.0        0.0   
5     payment delay for one month  ...   18055.0    18755.0    20299.0   
6     payment delay for one month  ...   17029.0    10575.0     9478.0   
7                         unknown  ...    -884.0    -6332.0    -9333.0   
8     payment delay for one month  ...  196467.0   201425.0    -8276.0   
9  payment delay for three months  ...   18472.0    18037.0    18487.0   

   PAY_AMT1  PAY_AMT2  PAY_AMT3  PAY_AMT4  PAY_AMT5  PAY_AMT6  \
0       0.0    1500.0    1600.0    1646.0     678.0    1000.0   
1       0.0    6216.0   10000.0       0.0    5000.0    4552.0   
2    1444.0   14019.0    1045.0   12525.0     244.0     725.0   
3    2400.0       0.0       0.0       0.0       0.0       0.0   
4      35.0       0.0       0.0    2920.0       0.0   12140.0   
5    1596.0    1600.0    1300.0    1000.0    2000.0       0.0   
6    2500.0    2000.0    2500.0     500.0     500.0     500.0   
7    1298.0    6730.0     900.0    5448.0       0.0   25000.0   
8    7028.0    6000.0   50000.0   10013.0    9505.0  175074.0   
9    3000.0   10000.0       0.0       0.0     900.0    2000.0   

   default payment next month  
0                           1  
1                           1  
2                           0  
3                           0  
4                           0  
5                           1  
6                           0  
7                           0  
8                           0  
9              

In [5]:
# Open the JSON file and read its contents
with open(f"{PROCESSED_DATA_DIR}/{DATA_NAME}/info.json", "r") as file:
    data_info = json.load(file)

# Display the JSON data
pprint(data_info)

{'cat_col_idx': [1, 2, 3, 5, 6, 7, 8, 9, 10],
 'column_info': {'0': {},
                 '1': {},
                 '10': {},
                 '11': {},
                 '12': {},
                 '13': {},
                 '14': {},
                 '15': {},
                 '16': {},
                 '17': {},
                 '18': {},
                 '19': {},
                 '2': {},
                 '20': {},
                 '21': {},
                 '22': {},
                 '23': {},
                 '3': {},
                 '4': {},
                 '5': {},
                 '6': {},
                 '7': {},
                 '8': {},
                 '9': {},
                 'categorizes': [0, 1],
                 'max': 528666.0,
                 'min': 0.0,
                 'type': 'categorical'},
 'column_names': ['LIMIT_BAL',
                  'SEX',
                  'EDUCATION',
                  'MARRIAGE',
                  'AGE',
                  'PAY_0',
   

# TabDDPM Algorithm

In this section, we will describe the design of TabDDPM as well as its main hyperparameters loaded through config, which affect the model’s effectiveness. 

**TabDDPM:** uses the multinomial diffusion to model the categorical and binary features, and the Gaussian diffusion to model the numerical ones. The model is trained using the diffusion process, which is a continuous-time Markov chain that models the data distribution. In more detail, for a tabular data sample that consists of N numerical featuresand C categorical features with Ki categories each, TabDDPM takes one-hot encoded versions of categorical features as an input, and normalized numerical features. The figure below illustrates the diffusion process for classification problems; t, y and l denote a diffusion timestep, a class label, and logits, respectively.

<p align="center">
<img src="figures/tabddpm.png" width="1000"/>
</p>

**Diffusion models:**  are likelihood-based generative models that handle the data through forward and reverse Markov processes. The forward process gradually adds noise to an initial sample x0 from the data distribution q(x0) sampling noise from the predefined distributions q(xt|xt−1) with variances {β1, ..., βT}.

<p align="center">
<img src="figures/forward.png" width="300"/>
</p>

The reverse diffusion proces gradually denoises a latent variable xT∼q(xT) and allows generating new data samples from q(x0). Distributions p(xt−1|xt) are usually unknown and approximated by a neural network with parameters θ.

<p align="center">
<img src="figures/backward.png" width="280"/>
</p>

**Gaussian diffusion models:** operate in continuous spaces where forward and reverse processes are characterized by Gaussian distributions:

<p align="center">
<img src="figures/gaussian.png" width="440"/>
</p>

While in general θ parameters are learned from the data by optimizing a variational lower bound, in practice for Gaussian modeling, this objective can be simplified to the sum of mean-squared errors between εθ(xt ,t) and ε over all timesteps t as follows:

<p align="center">
<img src="figures/gaussian_loss.png" width="330"/>
</p>

**Multinomial diffusion models:** are designed to generate categorical data where samples are a one-hot encoded categorical variable with K values. The multinomial forward diffusion process defines q(xt|xt−1) as a categorical distribution that corrupts the data by uniform noise over K classes: 

<p align="center">
<img src="figures/multinomial.png" width="440"/>
</p>

The reverse distribution pθ(xt−1|xt) is parameterized as q(xt−1|xt,xˆ0(xt,t)), where xˆ0 is predicted by a neural network. 

## Load Config

In this section, we will load the configuration file that contains the hyperparameters for the TabDDPM model. 

In [6]:
config_path = f"src/baselines/tabddpm/configs/{DATA_NAME}.toml"
## Tabddpm is trained unconditional in this repo but conditional in main paper
raw_config = src.load_config(config_path)

pprint(raw_config)

{'device': 'cuda:0',
 'diffusion_params': {'gaussian_loss_type': 'mse', 'num_timesteps': 1000},
 'eval': {'T': {'cat_encoding': 'one-hot',
                'cat_min_frequency': None,
                'cat_nan_policy': None,
                'normalization': 'quantile',
                'num_nan_policy': None,
                'seed': 0,
                'y_policy': 'default'},
          'type': {'eval_model': 'mlp', 'eval_type': 'synthetic'}},
 'model_params': {'is_y_cond': False,
                  'num_classes': 2,
                  'rtdl_params': {'d_layers': [1024, 2048, 2048, 1024],
                                  'dropout': 0.0}},
 'model_save_path': 'ckpt/default',
 'model_type': 'mlp',
 'num_numerical_features': 14,
 'parent_dir': 'configs/default',
 'real_data_path': 'Data/default',
 'sample': {'batch_size': 10000, 'num_samples': 27000, 'seed': 0},
 'sample_save_path': 'sampled/default',
 'seed': 0,
 'task_type': 'binclass',
 'train': {'T': {'cat_encoding': None,
                 '

The configuration file is a TOML file that contains the following hyperparameters:

1. **model_type:**  specifies the type of backbone model to be used for learning the denoising process. For Adult dataset, this should be set to "mlp". The reverse diffusion step in TabDDPM is modelled by a multi-layer neural network that has an output of the same dimensionality as x0, where the first N coordinates are the predictions of ε for the Gaussian diffusion and the rest are the predictions of x_ohe for the multinomial diffusions. This model takes as input the corrupted data xt and the timestep t, and outputs the denoised data xt−1 as follows:

<p align="center">
<img src="figures/architecture.png" width="440"/>
</p>

2. **model_params:** contains the hyperparameters for the backbone model. For the Adult dataset, we use an MLP model with the following hyperparameters:
    - is_y_cond: Whether the model is trained to be conditioned on the target value or not. By default, this should be set to True.
    - d_layers: The dimension of layers in the MLP model.
    - dropout: The dropout rate.


    
3. **task_type:** specifice the task type that we will use to conidition our training to and can be binclass (binary classification) or regression, depending on each dataset. For the Adult dataset, the task type is binclass. For classification datasets, we use a class- conditional model, i.e. pθ(xt−1|xt, y) is learned. For regression datasets, we consider a target value as an additional numerical feature, and the joint distribution is learned.

4. **diffusion_params:** contains number of total diffusion steps, the diffusion step size, and type of loss used to minimize the predicited noise in Gaussian diffusion. 

5. **train.main:** contains the basic hyperparameters for training the model such number of epochs (steps), the batch size (batch_size), the learning rate(lr), and the rate of weight decay (weight_decay).

6. **train.T:** contains the defined transformations on train data such as normalization, standardization, and one-hot encoding. 
    - For preprocessing numerical features, we use the gaussian quantile transformation and replace the Nan values with mean of each row. 
    - For categorical features, we use the one-hot encoding method. Each categorical feature is handled by a separate forward diffusion process, i.e., the noise components for all features are sampled independently. 

7. **sample:** contains the hyperparameters for sampling the data from the trained model. It includes the number of samples to generate, the batch size of sampling, and the seed used for random noise initialization.

8. **eval.T:** contains the defined transformations on evaluation data such as normalization, standardization, and one-hot encoding. 


## Make Dataset

Now that we have processed the data, we can create a dataset object. First we instantiate transformations needed for the dataset, such as normalization, standardization, and one-hot encoding in `T`. Next using make_dataset function we create a dataset object that contains the training and test data, as well as the column names, numerical column indices, and categorical column indices. This function takes the directory containing the processed data, the transformation and task type as input. Also it takes a boolean argument `change_val` that if it set true it will change the validation data to a split of train data rather than test data.
It returns a dataset object that contains the training and test data, as well as the column names, numerical column indices, and categorical column indices.

In [7]:
T = src.Transformations(**raw_config["train"]["T"])

dataset = make_dataset(
    f"{PROCESSED_DATA_DIR}/{DATA_NAME}",
    T,
    task_type=raw_config["task_type"],
    change_val=False,
)

data_path data//processed_data/default
No NaNs in numerical features, skipping


## Instantiate Model

Next, we instantiate the TabDDPM model. To do so first we need to apply some modifactions to loaded configs based on the dataset. We will set the number of numerical and size of one-hot coded categorical features based on the dataset.

In [9]:
dim_categorical_features = np.array(dataset.get_category_sizes("train"))
print("Each Categorical Features Size: ",dim_categorical_features)
if (
    len(dim_categorical_features) == 0
    or raw_config["train"]["T"]["cat_encoding"] == "one-hot"
):
    dim_categorical_features = np.array([0])

num_numerical_features = (
    dataset.X_num["train"].shape[1] if dataset.X_num is not None else 0
)
print("Numerical Features Size: ",num_numerical_features)

[ 2  2  7  4 11 11 11 11 10 10]


We will also set the input size of the model as sum of size of categorical plus length of numerical features.

In [10]:
dim_input = np.sum(dim_categorical_features) + num_numerical_features
raw_config["model_params"]["d_in"] = dim_input
print("Model Input Size:", dim_input)

93


Also we set device to be "cuda" if available otherwise we will use "cpu".

In [11]:
device = "cuda" if torch.cuda.is_available() else "cpu"

Finally, we will instantiate the model using the `TabDDPM` class. TabDDPM class takes the following arguments:

1. dataset: The dataset object containing the training and test data, as well as the column names, numerical column indices, and categorical column indices.
2. num_numerical_features: The number of numerical features in the dataset.
3. dim_categorical_features: The list of size of the one-hot encoded categorical features.
4. model_type: The type of backbone model to be used for learning the denoising process.
5. model_params: The hyperparameters for the backbone model.
6. diffusion_params: The hyperparameters for the diffusion process.
7. device: The device to use for training the model.

In [12]:
tabddpm = TabDDPM(
    dataset=dataset,
    num_numerical_features=num_numerical_features,
    num_classes=dim_categorical_features,
    model_type=raw_config["model_type"],
    model_params=raw_config["model_params"],
    device=device,
    **raw_config["diffusion_params"],
)

{'num_classes': 2, 'is_y_cond': False, 'rtdl_params': {'d_layers': [1024, 2048, 2048, 1024], 'dropout': 0.0}, 'd_in': 93}
mlp
the number of parameters 11734109


TabDDPM class first instantiates the backbone model, which is a multi-layer neural network that models the reverse diffusion process using `get_model` function. It then passes this model to `GaussianMultinomialDiffusion` class to initializes the diffusion process.

## Train Model

Now that we have instantiated the model, we can train it using the `train` function. This function takes the training arguments from the config file and path to save the trained model. It trains the model on the training data using the `Trainer` class. It returns the trained model and the training loss.

In [ ]:
tabddpm.train(
    **raw_config["train"]["main"],
    model_save_path=f"{MODEL_PATH}/{DATA_NAME}",
)

Steps:  100000
Step 1/100000 MLoss: 1.942 GLoss: 1.2893 Sum: 3.2313
Time:  1.3727469444274902
Step 2/100000 MLoss: 25.6218 GLoss: 19824.2422 Sum: 19849.864
Time:  0.47995901107788086
Step 3/100000 MLoss: 1.3565 GLoss: 1.321 Sum: 2.6775
Time:  0.9602108001708984
Step 4/100000 MLoss: 1.5919 GLoss: 1.1156 Sum: 2.7075
Time:  0.09085249900817871
Step 5/100000 MLoss: 1.2128 GLoss: 1.3265 Sum: 2.5393
Time:  0.15946745872497559
Step 6/100000 MLoss: 1.3601 GLoss: 1.9037 Sum: 3.2638
Time:  0.06458449363708496
Step 7/100000 MLoss: 1.3983 GLoss: 1.004 Sum: 2.4023000000000003
Time:  0.11879706382751465
Step 8/100000 MLoss: 1.2373 GLoss: 1.1612 Sum: 2.3985000000000003
Time:  0.1323094367980957
Step 9/100000 MLoss: 1.4819 GLoss: 1.8147 Sum: 3.2965999999999998
Time:  0.06536746025085449
Step 10/100000 MLoss: 1.1507 GLoss: 1.147 Sum: 2.2977
Time:  0.1397244930267334
Step 11/100000 MLoss: 1.2511 GLoss: 1.0291 Sum: 2.2802
Time:  0.13248777389526367
Step 12/100000 MLoss: 1.161 GLoss: 1.1271 Sum: 2.2881
Ti

Time:  0.13837575912475586
Step 101/100000 MLoss: 0.8829 GLoss: 0.9954 Sum: 1.8782999999999999
Time:  0.06253337860107422
Step 102/100000 MLoss: 0.9089 GLoss: 0.9936 Sum: 1.9025
Time:  0.06982254981994629
Step 103/100000 MLoss: 0.8459 GLoss: 1.0019 Sum: 1.8477999999999999
Time:  0.07203960418701172
Step 104/100000 MLoss: 0.875 GLoss: 0.9928 Sum: 1.8678
Time:  0.07332372665405273
Step 105/100000 MLoss: 0.8674 GLoss: 0.9826 Sum: 1.85
Time:  0.05178332328796387
Step 106/100000 MLoss: 0.8415 GLoss: 1.0117 Sum: 1.8532000000000002
Time:  0.07187628746032715
Step 107/100000 MLoss: 0.8896 GLoss: 1.0073 Sum: 1.8969
Time:  0.07157039642333984
Step 108/100000 MLoss: 0.846 GLoss: 1.0017 Sum: 1.8477000000000001
Time:  0.0706486701965332
Step 109/100000 MLoss: 0.9479 GLoss: 1.0018 Sum: 1.9497
Time:  0.07135820388793945
Step 110/100000 MLoss: 0.8374 GLoss: 1.0002 Sum: 1.8376000000000001
Time:  0.07135939598083496
Step 111/100000 MLoss: 0.8569 GLoss: 1.0059 Sum: 1.8628
Time:  0.07197737693786621
Step 

Time:  0.12316608428955078
Step 197/100000 MLoss: 0.7838 GLoss: 0.9951 Sum: 1.7789000000000001
Time:  0.06750249862670898
Step 198/100000 MLoss: 0.8023 GLoss: 1.006 Sum: 1.8083
Time:  0.07143926620483398
Step 199/100000 MLoss: 0.7413 GLoss: 0.9976 Sum: 1.7389000000000001
Time:  0.07148170471191406
Step 200/100000 MLoss: 0.7853 GLoss: 1.0071 Sum: 1.7924000000000002
Time:  0.07093524932861328
Step 201/100000 MLoss: 0.782 GLoss: 0.9991 Sum: 1.7811
Time:  0.07019495964050293
Step 202/100000 MLoss: 0.7718 GLoss: 0.9922 Sum: 1.764
Time:  0.07156825065612793
Step 203/100000 MLoss: 0.7679 GLoss: 0.9904 Sum: 1.7583
Time:  0.05103635787963867
Step 204/100000 MLoss: 0.7951 GLoss: 1.0008 Sum: 1.7959
Time:  0.07190132141113281
Step 205/100000 MLoss: 0.7845 GLoss: 1.0045 Sum: 1.789
Time:  0.07147431373596191
Step 206/100000 MLoss: 0.7766 GLoss: 1.0072 Sum: 1.7838
Time:  0.071441650390625
Step 207/100000 MLoss: 0.8146 GLoss: 1.0026 Sum: 1.8172
Time:  0.07163238525390625
Step 208/100000 MLoss: 0.7609 

Step 292/100000 MLoss: 0.7443 GLoss: 0.9903 Sum: 1.7346
Time:  0.07243919372558594
Step 293/100000 MLoss: 0.7809 GLoss: 0.9953 Sum: 1.7762
Time:  0.06922435760498047
Step 294/100000 MLoss: 0.7727 GLoss: 0.9831 Sum: 1.7558
Time:  0.048067331314086914
Step 295/100000 MLoss: 0.757 GLoss: 1.001 Sum: 1.758
Time:  0.07142186164855957
Step 296/100000 MLoss: 0.723 GLoss: 0.988 Sum: 1.7109999999999999
Time:  0.07413506507873535
Step 297/100000 MLoss: 0.7439 GLoss: 0.9865 Sum: 1.7304
Time:  0.07586264610290527
Step 298/100000 MLoss: 0.7218 GLoss: 0.999 Sum: 1.7208
Time:  0.07263445854187012
Step 299/100000 MLoss: 0.7052 GLoss: 0.9939 Sum: 1.6991
Time:  0.14257454872131348
Step 300/100000 MLoss: 0.7458 GLoss: 0.9971 Sum: 1.7429000000000001
Time:  0.06315135955810547
Step 301/100000 MLoss: 0.728 GLoss: 1.0029 Sum: 1.7308999999999999
Time:  0.04942178726196289
Step 302/100000 MLoss: 0.7667 GLoss: 0.9956 Sum: 1.7623000000000002
Time:  0.07117199897766113
Step 303/100000 MLoss: 0.7736 GLoss: 0.9988 S

Step 390/100000 MLoss: 0.7118 GLoss: 0.9827 Sum: 1.6945000000000001
Time:  0.07203173637390137
Step 391/100000 MLoss: 0.7611 GLoss: 0.9843 Sum: 1.7454
Time:  0.06960654258728027
Step 392/100000 MLoss: 0.7584 GLoss: 1.0028 Sum: 1.7611999999999999
Time:  0.04913735389709473
Step 393/100000 MLoss: 0.7379 GLoss: 0.987 Sum: 1.7248999999999999
Time:  0.06963992118835449
Step 394/100000 MLoss: 0.7458 GLoss: 0.9867 Sum: 1.7325
Time:  0.07274341583251953
Step 395/100000 MLoss: 0.7499 GLoss: 0.9861 Sum: 1.736
Time:  0.07146692276000977
Step 396/100000 MLoss: 0.7611 GLoss: 0.9916 Sum: 1.7527
Time:  0.07254791259765625
Step 397/100000 MLoss: 0.7207 GLoss: 0.9818 Sum: 1.7025000000000001
Time:  0.06991910934448242
Step 398/100000 MLoss: 0.7762 GLoss: 0.9763 Sum: 1.7525
Time:  0.07258009910583496
Step 399/100000 MLoss: 0.7183 GLoss: 0.976 Sum: 1.6943000000000001
Time:  0.048975229263305664
Step 400/100000 MLoss: 0.7173 GLoss: 0.9841 Sum: 1.7014
Time:  0.0722510814666748
Step 401/100000 MLoss: 0.7569 

...

Step 46806/100000 MLoss: 0.5268 GLoss: 0.3028 Sum: 0.8296000000000001
Time:  0.07848834991455078
Step 46807/100000 MLoss: 0.5382 GLoss: 0.3126 Sum: 0.8508
Time:  0.07829046249389648
Step 46808/100000 MLoss: 0.5038 GLoss: 0.3073 Sum: 0.8111
Time:  0.07837843894958496
Step 46809/100000 MLoss: 0.5235 GLoss: 0.3023 Sum: 0.8258
Time:  0.05481863021850586
Step 46810/100000 MLoss: 0.5365 GLoss: 0.3049 Sum: 0.8413999999999999
Time:  0.07868385314941406
Step 46811/100000 MLoss: 0.5359 GLoss: 0.3064 Sum: 0.8423
Time:  0.07918477058410645
Step 46812/100000 MLoss: 0.5319 GLoss: 0.2942 Sum: 0.8261000000000001
Time:  0.08014464378356934
Step 46813/100000 MLoss: 0.5389 GLoss: 0.3081 Sum: 0.847
Time:  0.07866978645324707
Step 46814/100000 MLoss: 0.5206 GLoss: 0.3013 Sum: 0.8219
Time:  0.0782623291015625
Step 46815/100000 MLoss: 0.5038 GLoss: 0.3077 Sum: 0.8115
Time:  0.07889366149902344
Step 46816/100000 MLoss: 0.521 GLoss: 0.3075 Sum: 0.8285
Time:  0.053261518478393555
Step 46817/100000 MLoss: 0.4961

Step 46902/100000 MLoss: 0.5215 GLoss: 0.2928 Sum: 0.8143
Time:  0.07883381843566895
Step 46903/100000 MLoss: 0.5465 GLoss: 0.2994 Sum: 0.8459
Time:  0.0796198844909668
Step 46904/100000 MLoss: 0.4999 GLoss: 0.299 Sum: 0.7988999999999999
Time:  0.07861876487731934
Step 46905/100000 MLoss: 0.52 GLoss: 0.2995 Sum: 0.8195
Time:  0.0795433521270752
Step 46906/100000 MLoss: 0.5054 GLoss: 0.2967 Sum: 0.8021
Time:  0.0779573917388916
Step 46907/100000 MLoss: 0.5373 GLoss: 0.2909 Sum: 0.8282
Time:  0.05300259590148926
Step 46908/100000 MLoss: 0.5378 GLoss: 0.293 Sum: 0.8308
Time:  0.07866215705871582
Step 46909/100000 MLoss: 0.5329 GLoss: 0.2964 Sum: 0.8293
Time:  0.07870221138000488
Step 46910/100000 MLoss: 0.5088 GLoss: 0.3029 Sum: 0.8117000000000001
Time:  0.07852935791015625
Step 46911/100000 MLoss: 0.509 GLoss: 0.2915 Sum: 0.8005
Time:  0.07848453521728516
Step 46912/100000 MLoss: 0.5229 GLoss: 0.299 Sum: 0.8219000000000001
Time:  0.07773089408874512
Step 46913/100000 MLoss: 0.5277 GLoss:

Step 46995/100000 MLoss: 0.5144 GLoss: 0.2965 Sum: 0.8109
Time:  0.08151912689208984
Step 46996/100000 MLoss: 0.5702 GLoss: 0.2932 Sum: 0.8634000000000001
Time:  0.07976388931274414
Step 46997/100000 MLoss: 0.5093 GLoss: 0.2908 Sum: 0.8001
Time:  0.07814741134643555
Step 46998/100000 MLoss: 0.4915 GLoss: 0.2967 Sum: 0.7882
Time:  0.055991172790527344
Step 46999/100000 MLoss: 0.5226 GLoss: 0.2931 Sum: 0.8157
Time:  0.07886385917663574
Step 47000/100000 MLoss: 0.5057 GLoss: 0.2978 Sum: 0.8035000000000001
Time:  0.07975316047668457
Step 47001/100000 MLoss: 0.5084 GLoss: 0.2926 Sum: 0.8009999999999999
Time:  0.08000445365905762
Step 47002/100000 MLoss: 0.5087 GLoss: 0.2984 Sum: 0.8071
Time:  0.07863354682922363
Step 47003/100000 MLoss: 0.5127 GLoss: 0.2939 Sum: 0.8066
Time:  0.07930374145507812
Step 47004/100000 MLoss: 0.5229 GLoss: 0.2905 Sum: 0.8134
Time:  0.07922172546386719
Step 47005/100000 MLoss: 0.5289 GLoss: 0.2931 Sum: 0.8220000000000001
Time:  0.05254626274108887
Step 47006/10000

Step 47091/100000 MLoss: 0.5285 GLoss: 0.3006 Sum: 0.8291
Time:  0.07948613166809082
Step 47092/100000 MLoss: 0.5085 GLoss: 0.2949 Sum: 0.8033999999999999
Time:  0.07851123809814453
Step 47093/100000 MLoss: 0.5227 GLoss: 0.3007 Sum: 0.8234000000000001
Time:  0.0777440071105957
Step 47094/100000 MLoss: 0.486 GLoss: 0.3009 Sum: 0.7868999999999999
Time:  0.07902789115905762
Step 47095/100000 MLoss: 0.5145 GLoss: 0.2968 Sum: 0.8112999999999999
Time:  0.07871174812316895
Step 47096/100000 MLoss: 0.4844 GLoss: 0.2988 Sum: 0.7832
Time:  0.0529177188873291
Step 47097/100000 MLoss: 0.5063 GLoss: 0.3018 Sum: 0.8081
Time:  0.0786433219909668
Step 47098/100000 MLoss: 0.5083 GLoss: 0.2923 Sum: 0.8006
Time:  0.07950615882873535
Step 47099/100000 MLoss: 0.5031 GLoss: 0.3029 Sum: 0.806
Time:  0.07894349098205566
Step 47100/100000 MLoss: 0.5362 GLoss: 0.3106 Sum: 0.8468
Time:  0.07832980155944824
Step 47101/100000 MLoss: 0.5391 GLoss: 0.3062 Sum: 0.8453
Time:  0.07811832427978516
Step 47102/100000 MLos

Step 47187/100000 MLoss: 0.5486 GLoss: 0.306 Sum: 0.8546
Time:  0.05559682846069336
Step 47188/100000 MLoss: 0.5253 GLoss: 0.3027 Sum: 0.8280000000000001
Time:  0.07961416244506836
Step 47189/100000 MLoss: 0.5382 GLoss: 0.3012 Sum: 0.8394
Time:  0.0794229507446289
Step 47190/100000 MLoss: 0.5297 GLoss: 0.302 Sum: 0.8316999999999999
Time:  0.07909464836120605
Step 47191/100000 MLoss: 0.505 GLoss: 0.3097 Sum: 0.8147
Time:  0.07921218872070312
Step 47192/100000 MLoss: 0.5091 GLoss: 0.3026 Sum: 0.8117
Time:  0.07778549194335938
Step 47193/100000 MLoss: 0.5 GLoss: 0.2989 Sum: 0.7988999999999999
Time:  0.07720494270324707
Step 47194/100000 MLoss: 0.4831 GLoss: 0.3156 Sum: 0.7987
Time:  0.05450606346130371
Step 47195/100000 MLoss: 0.5156 GLoss: 0.304 Sum: 0.8195999999999999
Time:  0.0785512924194336
Step 47196/100000 MLoss: 0.5075 GLoss: 0.2932 Sum: 0.8007
Time:  0.07925224304199219
Step 47197/100000 MLoss: 0.5167 GLoss: 0.3012 Sum: 0.8179000000000001
Time:  0.0784761905670166
Step 47198/1000

## Load pretrained Model

Instead of training model from scratch, we can also load weights of pre-trained model from give checkpoint with `load_model` function.

In [13]:
pretrained_model_path = "/projects/diffusion_bootcamp/models/tabular/tabddpm/default/model_100000.pt"

tabddpm.load_model(
    ckpt_path=pretrained_model_path,
)

Loaded model from /projects/diffusion_bootcamp/models/tabular/tabddpm/default/model_100000.pt


## Sample Data

Now that we trained the model effectively, using `sample` function we can generate synthetic data starting from compelete noise. The input of this function is as follows:

1. info_path: The path to the JSON file containing the information about the dataset.
2. num_samples: The number of samples to generate.
3. batch_size: The batch size for sampling the data.
4. sample_save_path: The path to save the generated samples.
5. ddim: Whether the sampling strategy is DDPM (Denoising Diffusion Probabilistic Models) and DDIM (Denoising Diffusion Implicit Models). DDPM produces high-quality samples but requires many computationally expensive sampling steps, making it slower. In contrast, DDIM (Denoising Diffusion Implicit Models) offers faster sampling with fewer steps by using a deterministic process, maintaining similar sample quality with improved efficiency. The choice between them depends on the need for speed versus the highest possible sample quality.
6. steps: The number of steps for sampling the data. This is the number of diffusion steps to take when sampling the data. The higher the number of steps, the better the quality of the generated samples.


In [14]:
tabddpm.sample(
    info_path=f"{PROCESSED_DATA_DIR}/{DATA_NAME}/info.json",
    num_samples=raw_config["sample"]["num_samples"],
    batch_size=raw_config["sample"]["batch_size"],
    sample_save_path=f"{SYNTH_DATA_DIR}/{DATA_NAME}/tabddpm.csv",
    ddim=True,
    steps=1000,
)

Sample using DDIM.
Sample timestep  999
Sample timestep  999
Sample timestep  999
Shape torch.Size([27000, 24])
(27000, 10)
Sampling time: 174.7004795074463


## Review Synthetic Data

Finally here, we review the synthesized data. In the following `evaluate_synthetic_data.ipynb` notebook, we will evaluate this synthesized data with respect to various metrics.

In [15]:
df = pd.read_csv(f"{SYNTH_DATA_DIR}/{DATA_NAME}/tabddpm.csv")

# Display the first few rows of the DataFrame
df.head(10)

LIMIT_BAL     SEX    EDUCATION MARRIAGE       AGE  \
0    50000.0    male  high school   single  27.00000   
1   140000.0  female       others   others  49.00000   
2   169398.1    male       others   others  45.00000   
3   150000.0    male  high school   single  36.00000   
4   360000.0  female       others   others  40.00000   
5    90000.0    male   university   single  25.00000   
6    20000.0  female       others   others  65.33677   
7   170000.0    male  high school   others  30.00000   
8    20000.0    male       others   single  22.00000   
9   150000.0  female   university   others  39.00000   

                            PAY_0                                    PAY_2  \
0   payment delay for five months            payment delay for five months   
1   payment delay for five months            payment delay for five months   
2  payment delay for eight months           payment delay for eight months   
3   payment delay for five months           payment delay for eight months   
4   payment delay for five months           payment delay for eight months   
5  payment delay for eight months  payment delay for nine months and above   
6   payment delay for five months            payment delay for five months   
7   payment delay for five months            payment delay for five months   
8   payment delay for four months  payment delay for nine months and above   
9   payment delay for five months            payment delay for five months   

                            PAY_3                           PAY_4  \
0   payment delay for five months   payment delay for five months   
1   payment delay for five months   payment delay for five months   
2  payment delay for eight months  payment delay for eight months   
3  payment delay for eight months  payment delay for eight months   
4   payment delay for five months   payment delay for five months   
5   payment delay for five months   payment delay for five months   
6   payment delay for five months   payment delay for five months   
7   payment delay for five months   payment delay for five months   
8   payment delay for five months   payment delay for five months   
9   payment delay for five months   payment delay for five months   

                            PAY_5  ...     BILL_AMT4     BILL_AMT5  \
0   payment delay for five months  ...   28808.79500   29009.39300   
1   payment delay for five months  ...   78044.88000   75261.17000   
2  payment delay for eight months  ...     212.52792     870.59717   
3  payment delay for eight months  ...     699.05190     696.44055   
4   payment delay for five months  ...  197005.66000  194259.81000   
5   payment delay for five months  ...   12165.85200   12287.77800   
6   payment delay for five months  ...    8953.34700    9609.05000   
7   payment delay for five months  ...  127367.19500  111890.97000   
8   payment delay for five months  ...    8998.49300    9572.64550   
9   payment delay for five months  ...   48810.77300   34934.32400   

     BILL_AMT6     PAY_AMT1     PAY_AMT2   PAY_AMT3   PAY_AMT4     PAY_AMT5  \
0   33054.1680    2373.2790   1669.02930  2819.0625  3000.0000   3000.00000   
1   80656.7700    3104.5479   3792.68000  3013.4587  2391.6530   3000.00000   
2       0.0000    3592.1301      0.00000     0.0000  1069.5513      0.00000   
3     598.5878    1000.0000   1481.43920  1000.0000  1000.0000    418.63895   
4  195125.8000  122782.4500  18071.09800  7000.0000  8326.6010   9444.16800   
5   12580.1740       0.0000    302.01077  1231.9579  1030.3462   1000.00000   
6   12486.3290    1400.3505   2082.26800  2442.7405   938.4309    780.00000   
7   96591.1200    5000.0000   6573.56900  5000.9663  4007.3887   3000.00000   
8    4744.4644       0.0000   1417.94170  1000.0000  1000.0000      0.00000   
9   63362.0040    4040.0237   3499.15060  2000.0000  1800.0000  29341.83800   

    PAY_AMT6  default payment next month  
0     0.0000                           1  
1  4501.6430                           0

## References

**Kotelnikov, Akim, et al.** "TABDDPM: Modeling tabular data with diffusion models." *Advances in Neural Information Processing Systems* 36 (2021).

**GitHub Repository:** [Amazon Science - Tabsyn](https://github.com/amazon-science/tabsyn)